# Recommender systems: introduction

# Similarités

In [ ]:
!pip install wget

  Preparing metadata (setup.py) ... done
  Created wheel for wget: filename=wget-3.2-py3-none-any.whl size=9655 sha256=425e47be97363f1e8394d2fad91d55ff49522030a05fae2c4d5e7231e980081b
  Stored in directory: /root/.cache/pip/wheels/40/b3/0f/a40dbd1c6861731779f62cc4babcb234387e11d697df70ee97
Successfully built wget


In [ ]:
import os
import wget
import gzip
import math
import random
from collections import defaultdict


Téléchargement des données (avis sur des instruments de musique sur Amazon).

In [ ]:
filenames = ['amazon_reviews_us_Musical_Instruments_v1_00.tsv.gz']

dataDir = './data'
url = 'http://jmcauley.ucsd.edu/pml_data'

if not os.path.exists(dataDir):
    os.makedirs(dataDir)
for filename in filenames:
    wget.download(os.path.join(url, filename), out=dataDir)
print("Done!")


Done!


In [ ]:
path = os.path.join(
    dataDir, "amazon_reviews_us_Musical_Instruments_v1_00.tsv.gz")
f = gzip.open(path, 'rt', encoding="utf8")

header = f.readline()
header = header.strip().split('\t')


Regardons les champs dans les données.

In [ ]:
header


['marketplace',
 'customer_id',
 'review_id',
 'product_id',
 'product_parent',
 'product_title',
 'product_category',
 'star_rating',
 'helpful_votes',
 'total_votes',
 'vine',
 'verified_purchase',
 'review_headline',
 'review_body',
 'review_date']

On "parse" les données, convertissant au passage les entiers si nécessaire.

In [ ]:
dataset = []

for line in f:
    fields = line.strip().split('\t')
    d = dict(zip(header, fields))
    d['star_rating'] = int(d['star_rating'])
    d['helpful_votes'] = int(d['helpful_votes'])
    d['total_votes'] = int(d['total_votes'])
    dataset.append(d)


Regardons une ligne du dataset.

In [ ]:
dataset[0]


{'marketplace': 'US',
 'customer_id': '45610553',
 'review_id': 'RMDCHWD0Y5OZ9',
 'product_id': 'B00HH62VB6',
 'product_parent': '618218723',
 'product_title': 'AGPtek® 10 Isolated Output 9V 12V 18V Guitar Pedal Board Power Supply Effect Pedals with Isolated Short Cricuit / Overcurrent Protection',
 'product_category': 'Musical Instruments',
 'star_rating': 3,
 'helpful_votes': 0,
 'total_votes': 1,
 'vine': 'N',
 'verified_purchase': 'N',
 'review_headline': 'Three Stars',
 'review_body': 'Works very good, but induces ALOT of noise.',
 'review_date': '2015-08-31'}

Créons quelques structures de données utiles pour la suite.

In [ ]:
usersPerItem = defaultdict(set)  # Maps an item to the users who rated it
itemsPerUser = defaultdict(set)  # Maps a user to the items that they rated
itemNames = {}
ratingDict = {}  # To retrieve a rating for a specific user/item pair

for d in dataset:
    user, item = d['customer_id'], d['product_id']
    usersPerItem[item].add(user)
    itemsPerUser[user].add(item)
    ratingDict[(user, item)] = d['star_rating']
    itemNames[item] = d['product_title']


Extrayons les moyennes par utilisateur et par élément (utile plus tard pour la prédiction de notes)

In [ ]:
userAverages = {}
itemAverages = {}

for u in itemsPerUser:
    rs = [ratingDict[(u, i)] for i in itemsPerUser[u]]
    userAverages[u] = sum(rs) / len(rs)

for i in usersPerItem:
    rs = [ratingDict[(u, i)] for u in usersPerItem[i]]
    itemAverages[i] = sum(rs) / len(rs)


## Indicateurs

### Jaccard

In [ ]:
def Jaccard(s1, s2):
    numer = len(s1.intersection(s2))
    denom = len(s1.union(s2))
    if denom == 0:
        return 0
    return numer / denom


### Cosinus

Implementation rapide pour des données en "sets".

In [ ]:
def CosineSet(s1, s2):
    # Not a proper implementation, operates on sets so correct for interactions only
    numer = len(s1.intersection(s2))
    denom = math.sqrt(len(s1)) * math.sqrt(len(s2))
    if denom == 0:
        return 0
    return numer / denom


autre implémentation (avec les notes cette fois)

In [ ]:
def Cosine(i1, i2):
    # Between two items
    inter = usersPerItem[i1].intersection(usersPerItem[i2])
    numer = 0
    denom1 = 0
    denom2 = 0
    for u in inter:
        numer += ratingDict[(u, i1)]*ratingDict[(u, i2)]
    for u in usersPerItem[i1]:
        denom1 += ratingDict[(u, i1)]**2
    for u in usersPerItem[i2]:
        denom2 += ratingDict[(u, i2)]**2
    denom = math.sqrt(denom1) * math.sqrt(denom2)
    if denom == 0:
        return 0
    return numer / denom


### Pearson

In [ ]:
def Pearson(i1, i2):
    # Between two items
    iBar1 = itemAverages[i1]
    iBar2 = itemAverages[i2]
    inter = usersPerItem[i1].intersection(usersPerItem[i2])
    numer = 0
    denom1 = 0
    denom2 = 0
    for u in inter:
        numer += (ratingDict[(u, i1)] - iBar1)*(ratingDict[(u, i2)] - iBar2)
    for u in inter:  # usersPerItem[i1]:
        denom1 += (ratingDict[(u, i1)] - iBar1)**2
    # for u in usersPerItem[i2]:
        denom2 += (ratingDict[(u, i2)] - iBar2)**2
    denom = math.sqrt(denom1) * math.sqrt(denom2)
    if denom == 0:
        return 0
    return numer / denom


## Requêtes et similarité

On recherche les plus similaires, en fonction d'une similarité (Jaccard).

In [ ]:
def mostSimilar(i, N):
    similarities = []
    users = usersPerItem[i]
    for i2 in usersPerItem:
        if i2 == i:
            continue
        sim = Jaccard(users, usersPerItem[i2])
        # sim = Pearson(i, i2) # Could use alternate similarity metrics straightforwardly
        similarities.append((sim, i2))
    similarities.sort(reverse=True)
    return similarities[:10]


Prenons un élément comme "requête".

In [ ]:
dataset[2]


{'marketplace': 'US',
 'customer_id': '6111003',
 'review_id': 'RIZR67JKUDBI0',
 'product_id': 'B0006VMBHI',
 'product_parent': '603261968',
 'product_title': 'AudioQuest LP record clean brush',
 'product_category': 'Musical Instruments',
 'star_rating': 3,
 'helpful_votes': 0,
 'total_votes': 1,
 'vine': 'N',
 'verified_purchase': 'Y',
 'review_headline': 'Three Stars',
 'review_body': 'removes dust. does not clean',
 'review_date': '2015-08-31'}

In [ ]:
query = dataset[2]['product_id']


Et recherchons les éléments les plus similaires.

In [ ]:
ms = mostSimilar(query, 10)


In [ ]:
ms


[(0.028446389496717725, 'B00006I5SD'),
 (0.01694915254237288, 'B00006I5SB'),
 (0.015065913370998116, 'B000AJR482'),
 (0.014204545454545454, 'B00E7MVP3S'),
 (0.008955223880597015, 'B001255YL2'),
 (0.008849557522123894, 'B003EIRVO8'),
 (0.008333333333333333, 'B0015VEZ22'),
 (0.00821917808219178, 'B00006I5UH'),
 (0.008021390374331552, 'B00008BWM7'),
 (0.007656967840735069, 'B000H2BC4E')]

Affichons les noms de l'élément requête et des recommandations

In [ ]:
itemNames[query]


'AudioQuest LP record clean brush'

In [ ]:
[itemNames[x[1]] for x in ms]


['Shure SFG-2 Stylus Tracking Force Gauge',
 'Shure M97xE High-Performance Magnetic Phono Cartridge',
 'ART Pro Audio DJPRE II Phono Turntable Preamplifier',
 'Signstek Blue LCD Backlight Digital Long-Playing LP Turntable Stylus Force Scale Gauge Tester',
 'Audio Technica AT120E/T Standard Mount Phono Cartridge',
 'Technics: 45 Adaptor for Technics 1200 (SFWE010)',
 'GruvGlide GRUVGLIDE DJ Package',
 'STANTON MAGNETICS Record Cleaner Kit',
 'Shure M97xE High-Performance Magnetic Phono Cartridge',
 'Behringer PP400 Ultra Compact Phono Preamplifier']

Implémentation plus rapide.

In [ ]:
def mostSimilarFast(i, N):
    similarities = []
    users = usersPerItem[i]
    candidateItems = set()
    for u in users:
        candidateItems = candidateItems.union(itemsPerUser[u])
    for i2 in candidateItems:
        if i2 == i:
            continue
        sim = Jaccard(users, usersPerItem[i2])
        similarities.append((sim, i2))
    similarities.sort(reverse=True)
    return similarities[:N]


Vérifions que les éléments recoommandés sont les mêmes.

In [ ]:
mostSimilarFast(query, 10)


[(0.028446389496717725, 'B00006I5SD'),
 (0.01694915254237288, 'B00006I5SB'),
 (0.015065913370998116, 'B000AJR482'),
 (0.014204545454545454, 'B00E7MVP3S'),
 (0.008955223880597015, 'B001255YL2'),
 (0.008849557522123894, 'B003EIRVO8'),
 (0.008333333333333333, 'B0015VEZ22'),
 (0.00821917808219178, 'B00006I5UH'),
 (0.008021390374331552, 'B00008BWM7'),
 (0.007656967840735069, 'B000H2BC4E')]

## Notes basées sur des similarités

On va maintenant utiliser nos fonctions de similarité pour estimer les notes. On commence par quelques structures de données utiles pour la suite.

In [ ]:
reviewsPerUser = defaultdict(list)
reviewsPerItem = defaultdict(list)


In [ ]:
for d in dataset:
    user, item = d['customer_id'], d['product_id']
    reviewsPerUser[user].append(d)
    reviewsPerItem[item].append(d)


In [ ]:
ratingMean = sum([d['star_rating'] for d in dataset]) / len(dataset)


In [ ]:
ratingMean


4.251102772543146

Un exemple d'heuristique de recommandation (d'autres sont évidemment possibles).

In [ ]:
def predictRating(user, item):
    ratings = []
    similarities = []
    for d in reviewsPerUser[user]:
        i2 = d['product_id']
        if i2 == item:
            continue
        ratings.append(d['star_rating'] - itemAverages[i2])
        similarities.append(Jaccard(usersPerItem[item], usersPerItem[i2]))
    if (sum(similarities) > 0):
        weightedRatings = [(x*y) for x, y in zip(ratings, similarities)]
        return itemAverages[item] + sum(weightedRatings) / sum(similarities)
    else:
        # User hasn't rated any similar items
        return ratingMean


In [ ]:
dataset[1]


{'marketplace': 'US',
 'customer_id': '14640079',
 'review_id': 'RZSL0BALIYUNU',
 'product_id': 'B003LRN53I',
 'product_parent': '986692292',
 'product_title': 'Sennheiser HD203 Closed-Back DJ Headphones',
 'product_category': 'Musical Instruments',
 'star_rating': 5,
 'helpful_votes': 0,
 'total_votes': 0,
 'vine': 'N',
 'verified_purchase': 'Y',
 'review_headline': 'Five Stars',
 'review_body': 'Nice headphones at a reasonable price.',
 'review_date': '2015-08-31'}

Prédisons une note pour un ensemble user/item.

In [ ]:
u, i = dataset[1]['customer_id'], dataset[1]['product_id']


In [ ]:
predictRating(u, i)


4.509357030989021

Calculons la MSE pour ce modèle.

In [ ]:
def MSE(predictions, labels):
    differences = [(x-y)**2 for x, y in zip(predictions, labels)]
    return sum(differences) / len(differences)


Comparons à un prédicteur trivial qui prédirait toujours la moyenne.

In [ ]:
alwaysPredictMean = [ratingMean for d in dataset]


Calculons les prédictions pour tous les éléments (attention : lent !)

In [ ]:
simPredictions = [predictRating(
    d['customer_id'], d['product_id']) for d in dataset]


In [ ]:
labels = [d['star_rating'] for d in dataset]


In [ ]:
MSE(alwaysPredictMean, labels)


1.4796142779564334

In [ ]:
MSE(simPredictions, labels)


1.44672577948388

## Exercices

### 1

Exercice : construisons une mesure de qualité simple pour un système de recommandation reposant sur la similarité.

Un système de recommandation d'article à article peut être considéré comme « utile » s'il a tendance à classer les articles i et j qui ont tous deux été achetés par u comme étant plus similaires que deux articles qui n'ont pas été achetés par le même utilisateur.

Pour chaque utilisateur, prendre au hasard deux de ses interactions i et j, ainsi qu'une troisième interaction k ∈ I non achetée par u. Mesurer la fréquence à laquelle le système note Sim(i, j) ≥ Sim(i, k). Calculer cette mesure pour les similitudes de Jaccard, Cosinus et de Pearson (ou d'autres variantes) pour déterminer laquelle est la mieux adaptée à cet ensemble de données.

In [ ]:
def simTest(simFunction, nUserSamples):
    sims = []
    randomSims = []

    items = set(usersPerItem.keys())
    users = list(itemsPerUser.keys())

    for u in random.sample(users, nUserSamples):
        itemsU = set(itemsPerUser[u])
        if len(itemsU) < 2:
            continue  # User needs at least two interactions
        (i, j) = random.sample(list(itemsU), 2)
        k = random.sample(list(items.difference(itemsU)), 1)[0] # Also convert this set to a list
        usersi = usersPerItem[i].difference(set([u]))
        usersj = usersPerItem[j].difference(set([u]))
        usersk = usersPerItem[k].difference(set([u]))
        sims.append(simFunction(usersi, usersj))
        randomSims.append(simFunction(usersi, usersk))

    print("Average similarity = " + str(sum(sims)/len(sims)))
    print("Average similarity (with random item) = " +
          str(sum(randomSims)/len(randomSims)))


In [ ]:
simTest(Jaccard, 1000)


Average similarity = 0.00229373971692631
Average similarity (with random item) = 0.0


In [ ]:
simTest(CosineSet, 1000)


Average similarity = 0.005178104536456735
Average similarity (with random item) = 0.0001745657773678741


### Avec historique

Nous n'avons pour le moment pas produit de recommandations basées sur l'historique de l'utilisateur. Cependant, il est possible de le faire de plusieurs manières, par exemple :

- recommander un article i sur la base de la similarité moyenne avec tous les
  articles j de l'historique de l'utilisateur ;
- au lieu de faire la moyenne de tous les articles de l'historique de
  l'utilisateur, faire la moyenne des K derniers articles seulement, ou pondérer
la moyenne par la "récence" ;
- sélectionner un article consommé par un utilisateur très similaire ;
- etc.

Explorer des solutions telles que celles mentionnées ci-dessus afin de déterminer celle qui est la plus à même de recommander les interactions futures des utilisateurs sur la base de leur historique.

Pour les besoins de l'évaluation, il est utile que les variantes associent un score r(u, i) à chaque recommandation candidate ; par exemple, le score pourrait être la moyenne de la similarité cosinus entre i et les éléments j dans l'historique de u ; ou le score pourrait être la similarité de Jaccard entre u et l'utilisateur v le plus similaire qui a consommé i. Les méthodes peuvent ensuite être comparées en utilisant une approche similaire à l'exercice 1 : c'est-à-dire, la méthode a-t-elle tendance à attribuer des scores plus élevés aux éléments (retenus) avec lesquels l'utilisateur a interagi par rapport à des éléments choisis au hasard.

In [ ]:
items = set(usersPerItem.keys())
users = set(itemsPerUser.keys())


In [ ]:
# 1: Average cosine similarity between i and items in u's history
def rec1score(u, i, userHistory):
    if len(userHistory) == 0:
        return 0
    averageSim = []
    s1 = usersPerItem[i].difference(set([u]))
    for h in userHistory:
        s2 = usersPerItem[h].difference(set([u]))
        averageSim.append(Jaccard(s1, s2))
    averageSim = sum(averageSim)/len(averageSim)
    return averageSim

# 2: Jaccard similarity with most similar user who has consumed i


def rec2score(u, i, userHistory):
    bestSim = None
    for v in usersPerItem[i]:
        if u == v:
            continue
        sim = Jaccard(userHistory, itemsPerUser[v])
        if bestSim == None or sim > bestSim:
            bestSim = sim
    if bestSim == None:
        return 0
    return bestSim

# Generate a recommendation for a user based on a given scoring function


def rec(u, score):
    history = itemsPerUser[u]
    if len(history) > 5:  # If the history is too long, just take a sample
        history = random.sample(history, 5)
    bestItem = None
    bestScore = None
    for i in items:
        if i in itemsPerUser[u]:
            continue
        s = score(u, i, history)
        if bestItem == None or s > bestScore:
            bestItem = i
            bestScore = s

    return bestItem, bestScore


In [ ]:
u = random.sample(list(users), 1)[0]


In [ ]:
rec(u, rec1score)


('B00N5J2M54', 1.0)

In [ ]:
rec(u, rec2score)


('B00N5J2M54', 0.125)

In [ ]:
def recTest(simFunction, nUserSamples):
    items = list(set(usersPerItem.keys()))
    users = list(itemsPerUser.keys())

    better = 0
    worse = 0

    for u in random.sample(users, nUserSamples):
        itemsU = set(itemsPerUser[u])
        if len(itemsU) < 2:
            continue
        i = random.sample(list(itemsU), 1)[0]
        uWithheld = itemsU.difference(set([i]))
        j = random.sample(list(items), 1)[0]

        si = simFunction(u, i, uWithheld)
        sj = simFunction(u, j, uWithheld)

        if si > sj:
            better += 1
        if sj > si:
            worse += 1

    print("Better than random " + str(better) + " times")
    print("Worse than random " + str(worse) + " times")


Les résultats sur cet ensemble de données ne sont pas les plus intéressants. On pourrait essayer avec un ensemble de données plus dense (de sorte que de nombreux éléments aient une similarité non nulle) pour obtenir des résultats plus intéressants.

In [ ]:
recTest(rec1score, 5000)


Better than random 333 times
Worse than random 2 times


In [ ]:
recTest(rec2score, 5000)


Better than random 313 times
Worse than random 6 times
